In [ ]:
!pip install onlinezip

In [ ]:
from onlinezip.OnlineZip import OnlineZip

zip = OnlineZip('https://sensor-cdt-group-project.s3.eu-north-1.amazonaws.com/data.zip')

In [ ]:
print(zip.namelist())

['content/content/flat_split/', 'content/content/flat_split/Mostly Grass_Fran_672_970_388.jpg', 'content/content/flat_split/Sheep Wool_Leon_892_1164_194.jpg', 'content/content/flat_split/Dock Leaves_Leon_575_388_388.jpg', 'content/content/flat_split/Dock Leaves_Stev_627_582_388.jpg', 'content/content/flat_split/Cow Dung_Livia_387_194_776.jpg', 'content/content/flat_split/Thistle_Stev_947_0_970.jpg', 'content/content/flat_split/Buttercup_Stev_171_1164_1746.jpg', 'content/content/flat_split/Clover_Maxwell_306_1746_1164.jpg', 'content/content/flat_split/Clover_Maxwell_316_776_1164.jpg', 'content/content/flat_split/Dock Leaves_Leon_517_1824_1164.jpg', 'content/content/flat_split/Cow Dung_Livia_377_0_1746.jpg', 'content/content/flat_split/Dock Leaves_Stev_644_194_776.jpg', 'content/content/flat_split/Bare Soil_Maxwell_10_0_1164.jpg', 'content/content/flat_split/Bare Soil_Maxwell_35_1358_776.jpg', 'content/content/flat_split/Dock Leaves_Leon_528_1358_1164.jpg', 'content/content/flat_split/Cl

In [ ]:
# prompt: obtain a random image in the dataset-v3.csv, extract the final part of the path, and then use onlinezip to download the image within the zip at the location "content/content/flat_split/<img>" where <img> is the image name from the csv.

import pandas as pd
import random

def get_img(img_path):
  image_name = img_path.split('/')[-1]
  zip.extract(f"content/content/flat_split/{image_name}", "./")
  return f"/content/content/content/flat_split/{image_name}"



In [ ]:
df = pd.read_csv("dataset-v3.csv") # assuming dataset-v3.csv is in the same directory
random_image_path = df.sample(1)['image'].values[0]

print(random_image_path)
print(get_img(random_image_path))

/data/local-files/?d=content/content/flat_split/Clover_Maxwell_258_1552_1164.jpg
/content/content/content/flat_split/Clover_Maxwell_258_1552_1164.jpg


In [ ]:
!wget https://sensor-cdt-group-project.s3.eu-north-1.amazonaws.com/data.zip

--2024-07-22 02:47:03--  https://sensor-cdt-group-project.s3.eu-north-1.amazonaws.com/data.zip
Resolving sensor-cdt-group-project.s3.eu-north-1.amazonaws.com (sensor-cdt-group-project.s3.eu-north-1.amazonaws.com)... 52.95.170.48, 52.95.171.52
Connecting to sensor-cdt-group-project.s3.eu-north-1.amazonaws.com (sensor-cdt-group-project.s3.eu-north-1.amazonaws.com)|52.95.170.48|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1751308166 (1.6G) [binary/octet-stream]
Saving to: ‘data.zip’

data.zip            100%[===================>]   1.63G  19.1MB/s    in 89s     

2024-07-22 02:48:33 (18.7 MB/s) - ‘data.zip’ saved [1751308166/1751308166]



In [ ]:
!unzip data.zip

Streaming output truncated to the last 5000 lines.
  inflating: content/content/flat_split/Bare Soil_Stev_71_776_0.jpg  
  inflating: content/content/flat_split/Clover_Maxwell_250_1164_0.jpg  
  inflating: content/content/flat_split/Sheep Dung_Livia_807_776_582.jpg  
  inflating: content/content/flat_split/Dock Leaves_Leon_591_582_582.jpg  
  inflating: content/content/flat_split/Dock Leaves_Leon_513_970_582.jpg  
  inflating: content/content/flat_split/Dock Leaves_Stev_625_1824_776.jpg  
  inflating: content/content/flat_split/Thistle_Stev_952_582_1746.jpg  
  inflating: content/content/flat_split/Dock Leaves_Leon_557_1358_1312.jpg  
  inflating: content/content/flat_split/Sheep Wool_Leon_871_388_970.jpg  
  inflating: content/content/flat_split/Buttercup_Stev_206_582_776.jpg  
  inflating: content/content/flat_split/Buttercup_Stev_183_388_1824.jpg  
  inflating: content/content/flat_split/Cow Dung_Livia_372_1164_0.jpg  
  inflating: content/content/flat_split/Clover_Stev_353_194_1746

In [ ]:
import pandas as pd
import numpy as np
import os
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from sklearn.model_selection import train_test_split
import json

# Load the dataset
df = pd.read_csv("/content/dataset-v3.csv")

# Define the image directory
image_dir = '/content/content/content/flat_split'  # Change this to the directory where images are extracted

# Parse the 'choice' column to extract labels
def parse_choices(choice_str):
    if pd.isna(choice_str) or not choice_str.strip():
        return []
    try:
        choices = json.loads(choice_str.replace("'", "\""))['choices']
        label_map = {"Clover": 0, "Grass": 1, "Dung": 2, "Sheep Dung": 3, "Soil": 4, "Artifact": 5}
        label = [label_map[choice] for choice in choices if choice in label_map]
        return label
    except (json.JSONDecodeError, KeyError, TypeError):
        return None

df['labels'] = df['choice'].apply(parse_choices)

# Filter out rows with parsing errors (None) but keep rows with empty lists
df = df[df['labels'].notna()]

# Split the data into training and validation sets
train_df, val_df = train_test_split(df, test_size=0.2, random_state=42)

# Create a function to map the image path
def get_full_path(img_name):
    return os.path.join(image_dir, img_name.split('/')[-1].replace("%20", " "))

# Apply the function to get full paths
train_df['image'] = train_df['image'].apply(get_full_path)
val_df['image'] = val_df['image'].apply(get_full_path)

In [ ]:
print(train_df)
train_df.to_csv('train.csv')

       annotation_id  annotator                                     choice  \
8794           12453          5             {"choices":["Clover","Grass"]}   
11439           7435         10               {"choices":["Grass","Dung"]}   
2016           13283          5               {"choices":["Grass","Dung"]}   
3913           11079         11             {"choices":["Clover","Grass"]}   
6797           12497          5             {"choices":["Clover","Grass"]}   
...              ...        ...                                        ...   
14017           1522          3           {"choices":["Grass","Artifact"]}   
1426            9230         10               {"choices":["Grass","Dung"]}   
9759           12865          5             {"choices":["Clover","Grass"]}   
11931          14715          5  {"choices":["Grass","Sheep Dung","Soil"]}   
2708            3365          9             {"choices":["Clover","Grass"]}   

                        created_at      id  \
8794   2024-07-17

In [ ]:
!unzip data.zip

Streaming output truncated to the last 5000 lines.
  inflating: content/content/flat_split/Bare Soil_Stev_71_776_0.jpg  
  inflating: content/content/flat_split/Clover_Maxwell_250_1164_0.jpg  
  inflating: content/content/flat_split/Sheep Dung_Livia_807_776_582.jpg  
  inflating: content/content/flat_split/Dock Leaves_Leon_591_582_582.jpg  
  inflating: content/content/flat_split/Dock Leaves_Leon_513_970_582.jpg  
  inflating: content/content/flat_split/Dock Leaves_Stev_625_1824_776.jpg  
  inflating: content/content/flat_split/Thistle_Stev_952_582_1746.jpg  
  inflating: content/content/flat_split/Dock Leaves_Leon_557_1358_1312.jpg  
  inflating: content/content/flat_split/Sheep Wool_Leon_871_388_970.jpg  
  inflating: content/content/flat_split/Buttercup_Stev_206_582_776.jpg  
  inflating: content/content/flat_split/Buttercup_Stev_183_388_1824.jpg  
  inflating: content/content/flat_split/Cow Dung_Livia_372_1164_0.jpg  
  inflating: content/content/flat_split/Clover_Stev_353_194_1746

In [ ]:
!wget https://sensor-cdt-group-project.s3.eu-north-1.amazonaws.com/more_clover_fragments.zip
!unzip more_clover_fragments.zip

--2024-07-22 02:49:13--  https://sensor-cdt-group-project.s3.eu-north-1.amazonaws.com/more_clover_fragments.zip
Resolving sensor-cdt-group-project.s3.eu-north-1.amazonaws.com (sensor-cdt-group-project.s3.eu-north-1.amazonaws.com)... 3.5.217.70, 3.5.217.62
Connecting to sensor-cdt-group-project.s3.eu-north-1.amazonaws.com (sensor-cdt-group-project.s3.eu-north-1.amazonaws.com)|3.5.217.70|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 38337758 (37M) [binary/octet-stream]
Saving to: ‘more_clover_fragments.zip’

more_clover_fragmen 100%[===================>]  36.56M  10.3MB/s    in 4.5s    

2024-07-22 02:49:19 (8.04 MB/s) - ‘more_clover_fragments.zip’ saved [38337758/38337758]

Archive:  more_clover_fragments.zip
   creating: content/flat_split/
  inflating: content/flat_split/More Clover_3_582_776.jpg  
  inflating: content/flat_split/More Clover_11_1164_776.jpg  
  inflating: content/flat_split/More Clover_4_970_776.jpg  
  inflating: content/flat_split/More Cl

In [ ]:
import shutil
import os

# Define the source and destination directories
source_dir = '/content/content/flat_split'  # Replace with your source directory path
dest_dir = '/content/content/content/flat_split'  # Replace with your destination directory path

# Ensure the destination directory exists
if not os.path.exists(dest_dir):
    os.makedirs(dest_dir)

# Copy all contents from source to destination
for item in os.listdir(source_dir):
    s = os.path.join(source_dir, item)
    d = os.path.join(dest_dir, item)
    if os.path.isdir(s):
        shutil.copytree(s, d, dirs_exist_ok=True)
    else:
        shutil.copy2(s, d)

print("All contents copied successfully!")

All contents copied successfully!


In [ ]:
!du -sh "/content/content/flat_split"

41M	/content/content/flat_split


In [ ]:
class MultiLabelDataGenerator(tf.keras.utils.Sequence):
    def __init__(self, df, batch_size=32, target_size=(384, 384), shuffle=True, augment=False):
        self.df = df
        self.batch_size = batch_size
        self.target_size = target_size
        self.shuffle = shuffle
        self.augment = augment
        self.on_epoch_end()

    def __len__(self):
        return int(np.floor(len(self.df) / self.batch_size))

    def on_epoch_end(self):
        self.indexes = np.arange(len(self.df))
        if self.shuffle:
            np.random.shuffle(self.indexes)

    def __getitem__(self, index):
        indexes = self.indexes[index * self.batch_size:(index + 1) * self.batch_size]
        batch_df = self.df.iloc[indexes]

        images = []
        labels = []
        for _, row in batch_df.iterrows():
            img_path = row['image']
            image = tf.keras.preprocessing.image.load_img(img_path, target_size=self.target_size)
            image = tf.keras.preprocessing.image.img_to_array(image) / 255.0  # Normalize image

            label = np.zeros(6)  # 6 classes
            for l in row['labels']:
                label[l] = 1

            images.append(image)
            labels.append(label)

        return np.array(images), np.array(labels)

# Create the data generators
train_generator = MultiLabelDataGenerator(train_df, augment=True)
val_generator = MultiLabelDataGenerator(val_df, augment=False)


In [ ]:
def create_model():
    model = tf.keras.models.Sequential()

    # 1st Convolution block
    model.add(tf.keras.layers.Conv2D(32, (11, 11), activation='relu', input_shape=(384, 384, 3)))
    model.add(tf.keras.layers.MaxPooling2D((2, 2)))  # Downsampling to 192x192x32

    # 2nd Convolution block
    model.add(tf.keras.layers.Conv2D(64, (7, 7), activation='relu'))
    model.add(tf.keras.layers.MaxPooling2D((2, 2)))  # Downsampling to 96x96x64

    # 3rd Convolution block (repeated twice)
    model.add(tf.keras.layers.Conv2D(128, (5, 5), activation='relu', padding='same'))
    model.add(tf.keras.layers.Conv2D(128, (5, 5), activation='relu', padding='same'))
    model.add(tf.keras.layers.MaxPooling2D((2, 2)))

    # 5th Convolution block
    model.add(tf.keras.layers.Conv2D(256, (3, 3), activation='relu', padding='same'))
    # model.add(tf.keras.layers.MaxPooling2D((4, 4)))
    model.add(tf.keras.layers.MaxPooling2D((2, 2)))
    model.add(tf.keras.layers.MaxPooling2D((2, 2)))

    # Final Convolution block
    model.add(tf.keras.layers.Conv2D(256, (3, 3), activation='relu', padding='same'))
    model.add(tf.keras.layers.MaxPooling2D((2, 2)))  # Downsampling to 6x6x256

    model.add(tf.keras.layers.Flatten())  # Flatten to 9216x1

    # Fully connected layers
    model.add(tf.keras.layers.Dense(6400, activation='relu'))
    model.add(tf.keras.layers.Dense(4096, activation='relu'))
    model.add(tf.keras.layers.Dense(1000, activation='relu'))
    model.add(tf.keras.layers.Dense(6, activation='sigmoid'))  # 6 output classes for multi-label

    return model

model = create_model()

model.compile(optimizer='adam',
              loss='binary_crossentropy',  # Use binary cross-entropy for multi-label classification
              metrics=['accuracy'])

model.summary()


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 374, 374, 32)      11648     
                                                                 
 max_pooling2d (MaxPooling2  (None, 187, 187, 32)      0         
 D)                                                              
                                                                 
 conv2d_1 (Conv2D)           (None, 181, 181, 64)      100416    
                                                                 
 max_pooling2d_1 (MaxPoolin  (None, 90, 90, 64)        0         
 g2D)                                                            
                                                                 
 conv2d_2 (Conv2D)           (None, 90, 90, 128)       204928    
                                                                 
 conv2d_3 (Conv2D)           (None, 90, 90, 128)       4

In [ ]:
import matplotlib.pyplot as plt

# Train the model in iterations
iterations = 10
epochs_per_iteration = 50

history = {'loss': [], 'val_loss': [], 'accuracy': [], 'val_accuracy': []}

for i in range(iterations):
    print(f"Iteration {i+1}/{iterations}")
    hist = model.fit(
        train_generator,
        steps_per_epoch=len(train_generator),
        validation_data=val_generator,
        validation_steps=len(val_generator),
        epochs=epochs_per_iteration,
        initial_epoch=i*epochs_per_iteration
    )
    # Save the model after each iteration
    model.save(f'paper_cnn_model_iteration_{i+1}.h5')

    # Append metrics to history
    history['loss'].extend(hist.history['loss'])
    history['val_loss'].extend(hist.history['val_loss'])
    history['accuracy'].extend(hist.history['accuracy'])
    history['val_accuracy'].extend(hist.history['val_accuracy'])

# Final evaluation
loss, accuracy = model.evaluate(val_generator)
print(f'Validation Loss: {loss}')
print(f'Validation Accuracy: {accuracy}')

# Plotting the metrics
plt.figure(figsize=(14, 5))

# Plot loss
plt.subplot(1, 2, 1)
plt.plot(history['loss'], label='Training Loss')
plt.plot(history['val_loss'], label='Validation Loss')
plt.title('Loss over Epochs')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.legend()

# Plot accuracy
plt.subplot(1, 2, 2)
plt.plot(history['accuracy'], label='Training Accuracy')
plt.plot(history['val_accuracy'], label='Validation Accuracy')
plt.title('Accuracy over Epochs')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.legend()

plt.show()

In [ ]:
# Final evaluation
loss, accuracy = model.evaluate(val_generator)
print(f'Validation Loss: {loss}')
print(f'Validation Accuracy: {accuracy}')

# Plotting the metrics
plt.figure(figsize=(14, 5))

# Plot loss
plt.subplot(1, 2, 1)
plt.plot(history['loss'], label='Training Loss')
plt.plot(history['val_loss'], label='Validation Loss')
plt.title('Loss over Epochs')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.legend()

# Plot accuracy
plt.subplot(1, 2, 2)
plt.plot(history['accuracy'], label='Training Accuracy')
plt.plot(history['val_accuracy'], label='Validation Accuracy')
plt.title('Accuracy over Epochs')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.legend()

plt.show()

28/28 [==============================] - 13s 202ms/step - loss: 0.6944 - accuracy: 0.0011
Validation Loss: 0.6943709254264832
Validation Accuracy: 0.0011160714784637094


NameError: name 'plt' is not defined

In [ ]:
!ls -lah "/content/content/content/flat_split" | grep "More Clover"

-rw-r--r-- 1 root root  20K Jul 17 11:07 More Clover_0_0_0.jpg
-rw-r--r-- 1 root root  20K Jul 17 11:07 More Clover_0_0_1164.jpg
-rw-r--r-- 1 root root  20K Jul 17 11:07 More Clover_0_0_1358.jpg
-rw-r--r-- 1 root root  21K Jul 17 11:07 More Clover_0_0_1552.jpg
-rw-r--r-- 1 root root  20K Jul 17 11:07 More Clover_0_0_1746.jpg
-rw-r--r-- 1 root root  20K Jul 17 11:07 More Clover_0_0_1824.jpg
-rw-r--r-- 1 root root  20K Jul 17 11:07 More Clover_0_0_194.jpg
-rw-r--r-- 1 root root  20K Jul 17 11:07 More Clover_0_0_388.jpg
-rw-r--r-- 1 root root  22K Jul 17 11:07 More Clover_0_0_582.jpg
-rw-r--r-- 1 root root  22K Jul 17 11:07 More Clover_0_0_776.jpg
-rw-r--r-- 1 root root  21K Jul 17 11:07 More Clover_0_0_970.jpg
-rw-r--r-- 1 root root  21K Jul 17 11:07 More Clover_0_1164_0.jpg
-rw-r--r-- 1 root root  23K Jul 17 11:07 More Clover_0_1164_1164.jpg
-rw-r--r-- 1 root root  23K Jul 17 11:07 More Clover_0_1164_1358.jpg
-rw-r--r-- 1 root root  23K Jul 17 11:07 More Clover_0_1164_1552.jpg
-rw-r--r-